# Tools

## Data preprocessing

In [23]:
%load_ext autoreload
%autoreload 2
import os
import random
import sqlite3 
import numpy as np
import json
import math
from tqdm.notebook import tqdm
from tqdm import tqdm
tqdm.pandas()

import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt

import Advan_operator as ad_op  

pd.set_option('display.max_columns', None)

import logging
# Create a logger
logger_name = 'all_logger'
logger = logging.getLogger(logger_name)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Load hourly population

#### Asign file locations

In [32]:
# data_dir = r'F:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'   # Lenovo

# Dell desktop
save_dir = r'D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\visualization'  # 2018 desktop
data_dir = r'D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018'  # Dell desktop
# data_dir = r'D:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'  
# data_dir = r'K:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'    
ACS_file = r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_data\Safegraph_bias\cbg_acs_2019_county_tract_new20230929_cleaned.csv"
# home_panel_fname = f"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\Monthly_Patterns_home_panel_summary_2019_2023.zip"
home_panel_fname = r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\home_panel_summary_2019_2023_restated_20240119.csv.gz"  ## large change!!!

# home_panel_fname = r"E:\OneDrive_PSU\OneDrive - The`1

# data_dir = r'K:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'   # Dell 
# save_dir = r'D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test'  # Dell
# ACS_file = r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_data\Safegraph_bias\cbg_acs_2019_county_tract_new20230929_cleaned.csv"
# home_panel_fname = f"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\Monthly_Patterns_home_panel_summary_2019_2023.zip"
# data_dir = r'F:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'   # Lenovo 
# save_dir = r'D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test'  # Lenovo
# ACS_file = r"F:\Research\Wild_fire\cbg_acs_2019_county_tract_new20230929_cleaned.csv"
# home_panel_fname = f"F:\SafeGraph\Advan_2023_API\Monthly_Patterns_home_panel_summary\Monthly_Patterns_home_panel_summary_2019_2023.csv"
# CBG_2019_fname = r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\blockgoups2019.zip"

# # 2018 desktop
# # save_dir = r'E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test'  # 2018 desktop
# save_dir = r'E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2023_home_panel'  # 2018 desktop
# # data_dir = r'D:\SafeGraph\Advan_2023_API\Neighborhood_Patterns'  
# data_dir = r'D:\SafeGraph\Advan_2024_API\Neighborhood_Patterns'    
# ACS_file = r"E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_data\Safegraph_bias\cbg_acs_2019_county_tract_new20230929_cleaned.csv"
# home_panel_fname = f"E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\Monthly_Patterns_home_panel_summary_2019_2023.zip"
home_panel_fname = r"E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\home_panel_summary_2019_2023_restated_20240119.csv.gz"  ## large change!!!
# # https://community.deweydata.io/t/residing-device-count-in-2023-07-and-2023-08-surged-abnomorally/26675/15
# CBG_2019_fname = r"E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\blockgoups2019.zip"


os.makedirs(save_dir, exist_ok=True)
save_file = True

year = '2023'
month = 8

 
month_dir = os.path.join(data_dir, str(year), f'{month:02}', '01')
no_dict_colum_fname = os.path.join(save_dir, f"NP_dict_column_{year}_{month:02}.csv")
device_home_areas_fname = os.path.join(save_dir, f"NP_split_device_home_areas_{year}_{month:02}.csv")
adjusted_dwelling_time_stop_CBG_fname     = os.path.join(save_dir, f"adjusted_dwelling_time_stop_CBG_{year}_{month:02}.csv")
adjusted_dwelling_time_stop_natinol_fname = os.path.join(save_dir, f"adjusted_dwelling_time_stop_natinol_{year}_{month:02}.csv")
person_per_device_fname = os.path.join(save_dir, f"person_per_device_{year}_{month:02}.csv")
restored_CBG_hourly_vistor_count_fname = os.path.join(save_dir, f"restored_hourly_vistor_count_CBG_{year}_{month:02}.csv")
restored_target_hourly_vistor_count_fname = os.path.join(save_dir, f"restored_hourly_vistor_count_target_{year}_{month:02}.csv")
CBG_device_stop_destination_distribution_fname  = os.path.join(save_dir, f"CBG_device_stop_destination_distribution_{year}_{month:02}.csv")
CBG_device_stop_origin_distribution_fname = os.path.join(save_dir, f"CBG_device_stop_origin_distribution_{year}_{month:02}.csv")
IPF_results_fname = os.path.join(data_dir, f"IPF_origin_outgoer_hourly_{year}{month:02}.csv")
CBG_hourly_population_fname = os.path.join(data_dir, f"CBG_population_hourly_{year}{month:02}.csv")


CBG_origin_outbound_distribution_sampling_rate_fname = os.path.join(data_dir, f"CBG_origin_outbound_distribution_sampling_rate_{year}{month:02}.csv")
CBG_destination_inbound_per_device_fname = os.path.join(data_dir, f"CBG_destination_inbound_per_device_{year}{month:02}.csv")

CBG_destination_inbound_fname = os.path.join(data_dir, f"CBG_destination_inbound_{year}{month:02}.csv")
inbound_hourly_df_fname = os.path.join(data_dir, f"inbound_hourly_{year}{month:02}.csv")
CBG_agregated_inbound_fname =  os.path.join(save_dir, f"CBG_agregated_inbound_{year}{month:02}.csv")
hourly_agregated_inbound_fname =  os.path.join(save_dir, f"hourly_agregated_inbound_{year}{month:02}.csv")

 
# month_dir = r'K:\SafeGraph\Advan_2023_API\Neighborhood_Patterns\2023\06\01'
# CBG_list_fname = r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\ACS_2019_CBG_list.csv"

sqlite_fname = r'F:\Research\Wild_fire\Neighborhood_202306.db'

print("Month directory:", month_dir)
print("Save_dir directory:", save_dir)
print("ACS_file:", ACS_file)
print("home_panel file name:", home_panel_fname)

print("No dict colum file name:", no_dict_colum_fname)
print("Device home areas file name:", device_home_areas_fname)
print("Device person_per_device file name:", person_per_device_fname)


print("Device adjusted_dwelling_time_stop_CBG_fname:", adjusted_dwelling_time_stop_CBG_fname)
print("Device adjusted_dwelling_time_stop_natinol_fname:", adjusted_dwelling_time_stop_natinol_fname)

print("Restored_hourly_vistor_count_CBG file name:   ", restored_CBG_hourly_vistor_count_fname)
print("Restored_hourly_vistor_count_target file name:", restored_target_hourly_vistor_count_fname)

print("CBG_device_stop_destination_distribution file name:   ", CBG_device_stop_destination_distribution_fname)
print("CBG_device_stop_origin_distribution file name:", CBG_device_stop_origin_distribution_fname)

print("IPF_results file name:", IPF_results_fname)
print("CBG hourly population file name:", CBG_hourly_population_fname)

print("CBG_origin_outbound_distribution_sampling_rate file name:", CBG_origin_outbound_distribution_sampling_rate_fname)


Month directory: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\2023\08\01
Save_dir directory: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\visualization
ACS_file: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_data\Safegraph_bias\cbg_acs_2019_county_tract_new20230929_cleaned.csv
home_panel file name: E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\home_panel_summary_2019_2023_restated_20240119.csv.gz
No dict colum file name: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\visualization\NP_dict_column_2023_08.csv
Device home areas file name: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\visualization\NP_split_device_home_areas_2023_08.

## Load monthly neighborhood patterns

In [3]:
# CBG_hourly_population_fname

In [4]:
hourly_population_map_df = pd.read_csv(CBG_hourly_population_fname, dtype={'CBG':str}).set_index('CBG')   #  = hourly_population_map_df.set_index('CBG')
hourly_population_map_df# = hourly_population_map_df.set_index('CBG') 

hour_1       hour_2       hour_3       hour_4       hour_5  \
CBG                                                                             
010010201001   549.097312   635.078543   650.931655   640.999688   591.340724   
010010201002   906.093940  1075.727806  1107.004686  1087.409736   989.436701   
010010202001   554.894698   688.025935   712.572506   697.194091   620.303364   
010010202002  1129.189645  1313.760559  1375.451481  1205.441060   881.038245   
010010203001  2001.098967  2368.451066  2436.182987  2393.748972  2181.582611   
...                   ...          ...          ...          ...          ...   
721537506011   878.878574   880.837446   881.198621   915.613469   879.840987   
721537506012  2603.565040  2610.945139  2573.868828  2515.360761  2511.098341   
721537506013   984.929037   987.814505  1015.993282   988.013214   986.346695   
721537506021  1579.106864  1597.404693  1574.513086  1574.200699  1572.638790   
721537506022   644.819257   683.932785   684.211524   646.435141   645.562007   

                   hour_6       hour_7       hour_8       hour_9      hour_10  \
CBG                                                                             
010010201001   785.295122   787.041095   236.144712   174.781678   869.509738   
010010201002   799.162262   551.949853   288.664308   167.600110   105.915075   
010010202001   470.973092   276.957035    70.326537   -24.686486   678.587874   
010010202002   712.048428   492.489880  1581.253784   778.520600  1724.162215   
010010203001  2520.227917  2717.261051  1396.404966  1372.258826  1238.676260   
...                   ...          ...          ...          ...          ...   
721537506011   877.643765   874.789043   892.533388   891.135381   897.351289   
721537506012  2502.820252  2492.065017  2490.219764  2552.217568  2616.798724   
721537506013  1003.845201  1020.375193  1029.720092  1006.925723   971.318014   
721537506021  1600.792365  1573.461017  1569.263658  1645.301058  1558.553483   
721537506022   650.133242   647.930087   639.316730   650.771725   700.357659   

                  hour_11      hour_12      hour_13      hour_14      hour_15  \
CBG                                                                             
010010201001  1574.317401  2080.039165   743.180725    41.964923   470.956659   
010010201002    28.308109   -48.189208  -107.513481   -94.436376   299.791880   
010010202001   317.006462  -194.041224  -240.599815  -230.336704  -240.563166   
010010202002  3011.746941  1536.427322  2178.950787  1274.920556  2874.203822   
010010203001   100.202204   -65.457229   538.458698   859.732387    99.128151   
...                   ...          ...          ...          ...          ...   
721537506011   868.742212   888.643522   874.102016   901.965925   908.743680   
721537506012  2536.548261  2514.001643  2549.857723  2569.645179  2578.687538   
721537506013   969.997921  1003.255152   981.510979   995.556799   981.511773   
721537506021  1619.690203  1587.283691  1586.337930  1602.139895  1570.745187   
721537506022   668.331233   655.115572   685.921669   723.639964   673.388167   

                  hour_16      hour_17      hour_18      hour_19      hour_20  \
CBG                                                                             
010010201001   366.886743  1077.613259  1289.830040  2825.102166   822.660190   
010010201002   237.703142   105.767072   130.563570   315.239367   518.332481   
010010202001   161.720077  -312.931087  -293.470418   869.052671    -5.124621   
010010202002  1072.553409   842.324914   830.434848   332.024800  1428.043855   
010010203001   294.245098   943.091899  1784.105254  1755.431695  1169.901189   
...                   ...          ...          ...          ...          ...   
721537506011   928.811375   942.319993   873.324087   875.221514   870.638537   
721537506012  2556.767780  2574.675839  2604.582421  2688.605115  2678.222371   
721537506013   994.279025   993.766660   973.45

In [5]:
print("Each hour's population (billion):" )
hourly_population_map_df.iloc[:, 1:].sum(axis=0) / 10**9

Each hour's population (billion):


hour_2      0.327508
hour_3      0.327504
hour_4      0.327510
hour_5      0.327491
hour_6      0.327444
              ...   
hour_740    0.327377
hour_741    0.327405
hour_742    0.327443
hour_743    0.327462
hour_744    0.327489
Length: 743, dtype: float64

In [6]:
ACS_df = pd.read_csv(ACS_file)
ACS_df["CBG_FIPS"] = ACS_df["fips"].astype(str).str.zfill(12)
ACS_df["CBG"] = ACS_df["fips"].astype(str).str.zfill(12)
ACS_df['county_FIPS'] = ACS_df['CBG'].astype(str).str[:5]
print("Total US population (million):",  ACS_df['totalpopulation'].sum() / 10**6)
ACS_df

Total US population (million): 328.016242


fips  totalpopulation  male  female  under5years  5to9years  \
0        10010201001              730   293     437           17         32   
1        10010201002             1263   614     649           98         54   
2        10010202001              835   393     442           52         89   
3        10010202002             1124   665     459           47         55   
4        10010203001             2774  1423    1351           55        258   
...              ...              ...   ...     ...          ...        ...   
220328  721537506011              883   480     403           48         78   
220329  721537506012             2523  1010    1513          227        175   
220330  721537506013              991   477     514           86         37   
220331  721537506021             1577   795     782           68         36   
220332  721537506022              648   335     313           43          0   

        10to14years  15to17years  18to24years  25to34years  35to44years  \
0                24           43          104           69           87   
1               123           23          152          131          159   
2                37           78           36           79          133   
3                42           19          101          210          166   
4               220           80          151          505          398   
...             ...          ...          ...          ...          ...   
220328          120           12           79           45          105   
220329           96           36          308          250          260   
220330          162           76          190           53           90   
220331           18           24           82          169          225   
220332            0           63           51          112           96   

        45to54years  55to64years  65to74years  75to84years  85yearsandover  \
0               126           96           94           23              15   
1               219          172           83           28              21   
2                76           91           90           68               6   
3               227          137           54           18              48   
4               336          380          216          133              42   
...             ...          ...          ...          ...             ...   
220328           70          120          169           24              13   
220329          436          197          394          106              38   
220330          191           89           17            0               0   
220331          272          254          232          188               9   
220332          100           47           83           53               0   

        whitealone  blackorafricanamericanalone  \
0              613                           60   
1             1072                           92   
2              276                          507   
3              483                          610   
4             1866                          557   
...            ...                          ...   
220328         719                            0   
220329        1946                           89   
220330         538                          227   
220331        1116                           23   
220332         320                            0   

        americanindianandalaskanativealone  asianalone  \
0                                        0           0   
1                                        0           2   
2                                        0           0   
3                                        0           0   
4                                        0          32   
...                                    ...         ...   
220328                                   0           0   
220329                                  51           0   
220330                                   0           0   
220331                              

## Show hourly population map

In [7]:
# Load data
hourly_population_map_df

hour_1       hour_2       hour_3       hour_4       hour_5  \
CBG                                                                             
010010201001   549.097312   635.078543   650.931655   640.999688   591.340724   
010010201002   906.093940  1075.727806  1107.004686  1087.409736   989.436701   
010010202001   554.894698   688.025935   712.572506   697.194091   620.303364   
010010202002  1129.189645  1313.760559  1375.451481  1205.441060   881.038245   
010010203001  2001.098967  2368.451066  2436.182987  2393.748972  2181.582611   
...                   ...          ...          ...          ...          ...   
721537506011   878.878574   880.837446   881.198621   915.613469   879.840987   
721537506012  2603.565040  2610.945139  2573.868828  2515.360761  2511.098341   
721537506013   984.929037   987.814505  1015.993282   988.013214   986.346695   
721537506021  1579.106864  1597.404693  1574.513086  1574.200699  1572.638790   
721537506022   644.819257   683.932785   684.211524   646.435141   645.562007   

                   hour_6       hour_7       hour_8       hour_9      hour_10  \
CBG                                                                             
010010201001   785.295122   787.041095   236.144712   174.781678   869.509738   
010010201002   799.162262   551.949853   288.664308   167.600110   105.915075   
010010202001   470.973092   276.957035    70.326537   -24.686486   678.587874   
010010202002   712.048428   492.489880  1581.253784   778.520600  1724.162215   
010010203001  2520.227917  2717.261051  1396.404966  1372.258826  1238.676260   
...                   ...          ...          ...          ...          ...   
721537506011   877.643765   874.789043   892.533388   891.135381   897.351289   
721537506012  2502.820252  2492.065017  2490.219764  2552.217568  2616.798724   
721537506013  1003.845201  1020.375193  1029.720092  1006.925723   971.318014   
721537506021  1600.792365  1573.461017  1569.263658  1645.301058  1558.553483   
721537506022   650.133242   647.930087   639.316730   650.771725   700.357659   

                  hour_11      hour_12      hour_13      hour_14      hour_15  \
CBG                                                                             
010010201001  1574.317401  2080.039165   743.180725    41.964923   470.956659   
010010201002    28.308109   -48.189208  -107.513481   -94.436376   299.791880   
010010202001   317.006462  -194.041224  -240.599815  -230.336704  -240.563166   
010010202002  3011.746941  1536.427322  2178.950787  1274.920556  2874.203822   
010010203001   100.202204   -65.457229   538.458698   859.732387    99.128151   
...                   ...          ...          ...          ...          ...   
721537506011   868.742212   888.643522   874.102016   901.965925   908.743680   
721537506012  2536.548261  2514.001643  2549.857723  2569.645179  2578.687538   
721537506013   969.997921  1003.255152   981.510979   995.556799   981.511773   
721537506021  1619.690203  1587.283691  1586.337930  1602.139895  1570.745187   
721537506022   668.331233   655.115572   685.921669   723.639964   673.388167   

                  hour_16      hour_17      hour_18      hour_19      hour_20  \
CBG                                                                             
010010201001   366.886743  1077.613259  1289.830040  2825.102166   822.660190   
010010201002   237.703142   105.767072   130.563570   315.239367   518.332481   
010010202001   161.720077  -312.931087  -293.470418   869.052671    -5.124621   
010010202002  1072.553409   842.324914   830.434848   332.024800  1428.043855   
010010203001   294.245098   943.091899  1784.105254  1755.431695  1169.901189   
...                   ...          ...          ...          ...          ...   
721537506011   928.811375   942.319993   873.324087   875.221514   870.638537   
721537506012  2556.767780  2574.675839  2604.582421  2688.605115  2678.222371   
721537506013   994.279025   993.766660   973.45

In [8]:
hour_cnt = hourly_population_map_df.shape[1] - 1
print("hour count:", hour_cnt)

hour count: 743


In [27]:
def get_county_FIPS_dict():
    # county_gdf = gpd.read_file(r'https://github.com/gladcolor/spatial_data/raw/master/cb_2019_us_county_20m.zip')
    county_gdf = gpd.read_file(r"D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\vectors\cb_2019_us_county_20m.zip")
    state_gdf = gpd.read_file(r'https://github.com/gladcolor/spatial_data/raw/master/cb_2019_us_state_20m.zip')
    county_gdf = county_gdf.merge(state_gdf[['STATEFP', 'STUSPS', 'NAME']], left_on='STATEFP', right_on='STATEFP', suffixes=['_county', '_state'])
    county_gdf = county_gdf.sort_values('GEOID')
    county_gdf['county_state'] = county_gdf['NAME_county'] + ', ' + county_gdf['STUSPS']
    county_gdf['GEOID'] = county_gdf['GEOID'].astype(str).str.zfill(5)
    county_FIPS_dict = county_gdf.set_index(['county_state'])['GEOID'].to_dict()
    county_df = county_gdf[['NAME_state', 'county_state', 'GEOID']]
    return county_FIPS_dict, county_df

county_FIPS_dict, county_df= get_county_FIPS_dict()

list(county_FIPS_dict.items())[0], list(county_FIPS_dict.items())[-1]
# county_FIPS_dict
county_df

NAME_state   county_state  GEOID
2483      Alabama    Autauga, AL  01001
2494      Alabama    Baldwin, AL  01003
2512      Alabama    Barbour, AL  01005
2506      Alabama       Bibb, AL  01007
2471      Alabama     Blount, AL  01009
...           ...            ...    ...
1910  Puerto Rico  Vega Baja, PR  72145
1919  Puerto Rico    Vieques, PR  72147
1882  Puerto Rico   Villalba, PR  72149
1876  Puerto Rico    Yabucoa, PR  72151
1874  Puerto Rico      Yauco, PR  72153

[3220 rows x 3 columns]

In [ ]:
# type(county_gdf)

In [ ]:
# CBG2019_gdf = gpd.read_file(CBG_2019_fname)
# CBG2019_gdf['county_FIPS'] = CBG2019_gdf['GEOID'].astype(str).str.zfill(12).str[:5]
# CBG2019_gdf['CBG'] = CBG2019_gdf['GEOID'].astype(str).str.zfill(12) 
# CBG2019_gdf

In [ ]:
hourly_population_map_df.iloc[:, :hour_cnt ]

In [50]:
CBG_hourly_outbound_df = pd.read_csv(IPF_results_fname, dtype={'CBG':str}).set_index('CBG')
CBG_hourly_outbound_df

Unnamed: 0      hour_1      hour_2      hour_3      hour_4  \
CBG                                                                        
010010201001           0  180.902688   94.921457   79.068345   89.000312   
010010201002           1  356.906060  187.272194  155.995314  175.590264   
010010202001           2  280.105302  146.974065  122.427494  137.805909   
010010202002           3  316.981566  166.323411  138.545249  155.948254   
010010203001           4  772.901033  405.548934  337.817013  380.251028   
...                  ...         ...         ...         ...         ...   
721537506011      219278    4.121426    2.162554    1.801379    2.027655   
721537506012      219279   15.527573    8.147473    6.786740    7.639239   
721537506013      219280    6.070963    3.185495    2.653476    2.986786   
721537506021      219281    5.689879    2.985537    2.486914    2.799301   
721537506022      219282    3.180743    1.668968    1.390229    1.564859   

                  hour_5       hour_6       hour_7       hour_8       hour_9  \
CBG                                                                            
010010201001  138.659276   235.102462   360.405431   493.855288   555.218322   
010010201002  273.563299   463.837738   711.050147   974.335692  1095.399890   
010010202001  214.696636   364.026908   558.042965   764.673463   859.686486   
010010202002  242.961755   411.951572   631.510120   865.343819   972.865443   
010010203001  592.417389  1004.467859  1539.820849  2109.981157  2372.152787   
...                  ...          ...          ...          ...          ...   
721537506011    3.159013     5.356235     8.210957    11.251286    12.649293   
721537506012   11.901659    20.179748    30.934983    42.389497    47.656523   
721537506013    4.653305     7.889869    12.094946    16.573426    18.632725   
721537506021    4.361210     7.394609    11.335727    15.533086    17.463119   
721537506022    2.437993     4.133717     6.336872     8.683270     9.762192   

                  hour_10      hour_11      hour_12      hour_13      hour_14  \
CBG                                                                             
010010201001   586.484221   625.820366   664.594071   694.663385   688.035077   
010010201002  1157.084925  1234.691891  1311.189208  1370.513481  1357.436376   
010010202001   908.097839   969.004966  1029.041224  1075.599815  1065.336704   
010010202002  1027.650221  1096.575858  1164.515975  1217.204071  1205.589807   
010010203001  2505.735354  2673.797796  2839.457229  2967.927425  2939.608186   
...                   ...          ...          ...          ...          ...   
721537506011    13.361610    14.257788    15.141152    15.826208    15.675198   
721537506012    50.340195    53.716567    57.044663    59.625628    59.056695   
721537506013    19.681986    21.002079    22.303296    23.312401    23.089960   
721537506021    18.446517    19.683745    20.903283    21.849044    21.640566   
721537506022    10.311929    11.003561    11.685305    12.214002    12.097459   

                  hour_15      hour_16      hour_17      hour_18      hour_19  \
CBG                                                                             
010010201001   694.639716   726.110237   741.377680   728.809238   645.525030   
010010201002  1370.466783  1432.555521  1462.676926  1437.880427  1273.567564   
010010202001  1075.563166  1124.291351  1147.931087  1128.470418   999.515185   
010010202002  1217.162597  1272.305918  1299.057859  1277.035165  1131.102791   
010010203001  2967.826299  3102.283107  3167.512776  3113.814503  2757.985348   
...                   ...          ...          ...          ...          ...   
721537506011    15.825669    16.542648    16.890479    16.604138    14.706711   
721537506012    59.623597    62.324832    63.635296    62.556498    55.407894   
721537506013    23.311606    24.367734    24.880099    24.458311    21.663353   
721537506021    21.848300    22.838133 

In [51]:
CBG_hourly_inbound_df = pd.read_csv(inbound_hourly_df_fname, dtype={'CBG':str}).set_index('CBG')
CBG_hourly_inbound_df

hour_1     hour_2      hour_3      hour_4     hour_5  \
CBG                                                                      
010010201001    0.000000    0.00000    0.000000    0.000000   0.000000   
010010201002    0.000000    0.00000    0.000000    0.000000   0.000000   
010010202001    0.000000    0.00000    0.000000    0.000000   0.000000   
010010202002  322.171211  356.08397  389.996729  237.389314   0.000000   
010010203001    0.000000    0.00000    0.000000    0.000000   0.000000   
...                  ...        ...         ...         ...        ...   
780309611001   13.737627    0.00000    0.000000   13.737627  54.950508   
780309611002    0.000000    0.00000    0.000000    0.000000   0.000000   
780309612001   53.382081    0.00000    0.000000   44.485068   0.000000   
780309612002    0.000000    0.00000  125.257847    0.000000   0.000000   
780309900000    0.000000    0.00000    0.000000    0.000000   0.000000   

                  hour_6       hour_7       hour_8      hour_9      hour_10  \
CBG                                                                           
010010201001  290.397584   417.446526     0.000000    0.000000   725.993959   
010010201002    0.000000     0.000000     0.000000    0.000000     0.000000   
010010202001    0.000000     0.000000     0.000000    0.000000   751.685714   
010010202002    0.000000     0.000000  1322.597604  627.386043  1627.812436   
010010203001  750.695776  1483.081900   732.386123  970.411613   970.411613   
...                  ...          ...          ...         ...          ...   
780309611001   96.163389   164.851523   206.064404  274.752539   233.539658   
780309611002  156.202789   140.582510    31.240558  203.063626   452.988089   
780309612001    0.000000     0.000000    17.794027   71.176108    44.485068   
780309612002    0.000000   125.257847   375.773542  375.773542   313.144618   
780309900000    0.000000     0.000000     0.000000    0.000000    82.974062   

                  hour_11      hour_12      hour_13      hour_14      hour_15  \
CBG                                                                             
010010201001  1470.137767  2014.633236   707.844110     0.000000   435.596375   
010010201002     0.000000     0.000000     0.000000     0.000000   407.258663   
010010202001   451.011428     0.000000     0.000000     0.000000     0.000000   
010010202002  2984.322799  1576.943297  2272.154858  1356.510363  2967.366419   
010010203001     0.000000     0.000000   732.386123  1025.340573   292.954449   
...                   ...          ...          ...          ...          ...   
780309611001   535.767451   425.866435   563.242705   549.505078   329.703047   
780309611002   234.304184   234.304184   765.393668   203.063626   124.962231   
780309612001    35.588054     0.000000    17.794027     0.000000     0.000000   
780309612002   292.268310   229.639387   271.392002   438.402465   459.278773   
780309900000    66.379250    16.594812    16.594812     0.000000   199.137749   

                  hour_16      hour_17      hour_18      hour_19      hour_20  \
CBG                                                                             
010010201001   362.996980  1088.990939  1288.639277  2740.627195   635.244714   
010010201002   407.258663   305.443997   305.443997   325.806930   325.806930   
010010202001   451.011428     0.000000     0.000000  1033.567856     0.000000   
010010202002  1220.859327  1017.382772   983.470013   339.127591  1254.772086   
010010203001   622.528205  1336.604675  2123.919758  1739.417043   714.076470   
...                   ...          ...          ...          ...          ...   
780309611001   425.866435   233.539658   302.227793   261.014912   247.277285   
780309611002   374.886694   484.228647   390.506973   203.063626   156.202789   
780309612001     0.000000     0.000000    17.794027    71.176108     0.000000   
780309612002   271.392002   438.402465   626.289236   208.763079   354.897234   
7

In [56]:
# hourly outbound
CBG_hourly_outbound_df['county_FIPS'] = CBG_hourly_outbound_df.reset_index()['CBG'].astype(str).str[:5].to_list()
target_hourly_outbound_df = CBG_hourly_outbound_df[CBG_hourly_outbound_df['county_FIPS'].isin(['36061'] )]
target_hourly_outbound_df = target_hourly_outbound_df.drop(columns=['county_FIPS'])
target_hourly_outbound_df

Unnamed: 0      hour_1      hour_2      hour_3      hour_4  \
CBG                                                                        
360610001001      134724    0.000000    0.000000    0.000000    0.000000   
360610002011      134725   50.385909   26.437993   22.022506   24.788806   
360610002012      134726  188.403442   98.857178   82.346750   92.690525   
360610002020      134727    0.000000    0.000000    0.000000    0.000000   
360610002021      134728  147.271584   77.274879   64.368974   72.454517   
...                  ...         ...         ...         ...         ...   
360610317041      135823  137.136998   71.957160   59.939383   67.468515   
360610317042      135824  116.270261   61.008173   50.819019   57.202519   
360610317043      135825  139.858592   73.385208   61.128928   68.807481   
360610317044      135826  288.357039  151.303834  126.034135  141.865589   
360610319001      135827    0.000000    0.000000    0.000000    0.000000   

                  hour_5      hour_6      hour_7      hour_8      hour_9  \
CBG                                                                        
360610001001    0.000000    0.000000    0.000000    0.000000    0.000000   
360610002011   38.620066   65.481898  100.381899  137.551011  154.642146   
360610002012  144.408495  244.850497  375.348894  514.331971  578.239296   
360610002020    0.000000    0.000000    0.000000    0.000000    0.000000   
360610002021  112.881525  191.395232  293.403483  402.044057  451.999264   
...                  ...         ...         ...         ...         ...   
360610317041  105.113513  178.224250  273.212740  374.377146  420.894654   
360610317042   89.119462  151.105685  231.640745  317.411995  356.851409   
360610317043  107.199575  181.761254  278.634867  381.806961  429.247647   
360610317044  221.021472  374.750926  574.482581  787.200292  885.012342   
360610319001    0.000000    0.000000    0.000000    0.000000    0.000000   

                 hour_10     hour_11      hour_12      hour_13      hour_14  \
CBG                                                                           
360610001001    0.000000    0.000000     0.000000     0.000000     0.000000   
360610002011  163.350479  174.306576   185.106020   193.481073   191.634924   
360610002012  610.801570  651.768707   692.150084   723.466159   716.563022   
360610002020    0.000000    0.000000     0.000000     0.000000     0.000000   
360610002021  477.452608  509.475883   541.041279   565.520492   560.124434   
...                  ...         ...          ...          ...          ...   
360610317041  444.596411  474.415984   503.809187   526.603848   521.579123   
360610317042  376.946711  402.228944   427.149684   446.475914   442.215750   
360610317043  453.419784  483.831150   513.807685   537.054725   531.930280   
360610317044  934.849866  997.551280  1059.356171  1107.286351  1096.720895   
360610319001    0.000000    0.000000     0.000000     0.000000     0.000000   

                  hour_15      hour_16      hour_17      hour_18      hour_19  \
CBG                                                                             
360610001001     0.000000     0.000000     0.000000     0.000000     0.000000   
360610002011   193.474481   202.239806   206.492169   202.991545   179.794816   
360610002012   723.441508   756.216889   772.117365   759.027798   672.290384   
360610002020     0.000000     0.000000     0.000000     0.000000     0.000000   
360610002021   565.501223   591.121149   603.550265   593.318386   525.517308   
...                   ...          ...          ...          ...          ...   
360610317041   526.585905   550.442780   562.016579   552.488813   489.353508   
360610317042   446.460701   466.687519   476.500251   468.422228   414.893578   
360610317043   537.036426   561.366759   573.170250   563.453398   499.065122   
360610317044  1107.248622  1157.412311  1181.748460  1161.714491  1028.960313   
360610319001     0.000000     0.0000

In [54]:
import warnings

# Suppress all future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

cmap = 'viridis'
# day = 18

target_county = 'New York, NY'
target_county = 'Centre, PA'
target_county = 'Richland, SC'
target_county = 'Lexington, SC'
target_county = 'Union, NJ'
target_county = 'Fairfax, VA'
target_county = 'Los Angeles, CA'
target_county = 'Cook, IL'
target_county = 'Harris, TX'
target_county = 'Maricopa, AZ'
target_county = 'San Diego, CA'
target_county = 'Orange, CA'
target_county = 'Miami-Dade, FL'
target_county = 'Dallas, TX'
target_county = 'King, WA'
target_county = 'Riverside, CA'
target_county = 'Hudson, NJ'
target_county = 'Essex, NJ'
target_county = 'Berkshire, MA'



def draw_county_map(target_county):
    
    county_FIPS = county_FIPS_dict[target_county]
    
    target_counties = [county_FIPS] # ['36061']   # 06039

    # hourly population
    hourly_population_map_df['county_FIPS'] = hourly_population_map_df.reset_index()['CBG'].astype(str).str[:5].to_list()
    target_hourly_popu_df = hourly_population_map_df[hourly_population_map_df['county_FIPS'].isin(target_counties)]
    target_hourly_popu_df = target_hourly_popu_df.drop(columns=['county_FIPS'])

    # hourly inbound
    CBG_hourly_inbound_df['county_FIPS'] = CBG_hourly_inbound_df.reset_index()['CBG'].astype(str).str[:5].to_list()
    target_hourly_inbound_df = CBG_hourly_inbound_df[CBG_hourly_inbound_df['county_FIPS'].isin(target_counties)]
    target_hourly_inbound_df = target_hourly_inbound_df.drop(columns=['county_FIPS'])

    # hourly outbound
    CBG_hourly_outbound_df['county_FIPS'] = CBG_hourly_outbound_df.reset_index()['CBG'].astype(str).str[:5].to_list()
    target_hourly_outbound_df = CBG_hourly_outbound_df[CBG_hourly_outbound_df['county_FIPS'].isin(target_counties)]
    target_hourly_outbound_df = target_hourly_outbound_df.drop(columns=['county_FIPS'])

 
    target_hourly_county_popu_df = pd.DataFrame(target_hourly_popu_df.sum(axis=0), columns=['hourly_population'])
    # print(target_hourly_county_popu_df)

    
    
    
    
    # target_blockgroup_gdf = CBG2019_gdf[CBG2019_gdf['county_FIPS'].isin(target_counties)]
    # target_blockgroup_gdf
    
    # row_cnt = 2
    # col_cnt = 13
    # fig, axs = plt.subplots(figsize=(40, 10), nrows=row_cnt, ncols=col_cnt)
    fig, ax = plt.subplots(figsize=(40, 10))

    # Generate hourly list
    start_date = pd.to_datetime(f'{year}-{month:02d}-01')
    _, last_month_day = calendar.monthrange(year, month)
    # end_date = f"{year}-{month:02d}-{last_month_day:02d}"
    next_month = month + 1
    # print("month, next_month", month, next_month)
    end_date = f"{year}-{next_month:02d}-01"
    
    hourly_list = pd.date_range(start_date, end_date, freq='H')
    # print(month, hourly_list)
    
    
    target_hourly_county_popu_df.plot(ax=ax)
    target_hourly_inbound_df.plot(ax=ax)
    target_hourly_outbound_df.plot(ax=ax)

    target_hourly_county_popu_df.index = hourly_list[:-1]

    county_ACS_popu_df = ACS_df[ACS_df['county_FIPS'].isin(target_counties)] 

    print("target_counties:", target_counties)
    # print("county_ACS_popu_df:", county_ACS_popu_df)
    ax.axhline(county_ACS_popu_df['totalpopulation'].sum(), color='red', label='ACS population')
    ax.legend()


    # # vmax = max(target_hourly_pop_df.iloc[:, :hour_cnt].max(axis=1).max(), target_pop_df['totalpopulation'].max())
    # # vmax = target_hourly_pop_df.iloc[:, :hour_cnt ].mean(axis=1).mean() + target_hourly_pop_df.iloc[:, :hour_cnt].mean(axis=1).std() * 3
    # # print("target_hourly_pop_df:\n", target_hourly_pop_df.iloc[:, 1: hour_cnt + 1].mean(axis=1).mean())
    # # print(target_hourly_pop_df)
    
    # vmax = target_hourly_pop_df.iloc[:, : hour_cnt].mean(axis=1).mean() + target_hourly_pop_df.iloc[:, :hour_cnt ].mean(axis=1).std() * 3
    
    # print("vmax: ", vmax)
    
    # 
    # # draw hourly map
    # used_ax_cnt = 0
    # hour_24_pop = []
    # for row in range(row_cnt):
    #     for col in range(1, col_cnt, 1):
    #         # if used_ax_cnt == 24:
    #         #     continue
    #         merged_gdf = target_blockgroup_gdf.merge(target_hourly_pop_df, left_on='CBG', right_on='CBG')
    #         hour = used_ax_cnt
    #         ax=axs[row, col]
    #         ax.axis('off')
    #         ax.set_title(f"{hour:02}:00:00")
    #         hour_column = f'hour_{hour + 1 + 24*(day - 1)}'
    #         merged_gdf.plot(column=hour_column, ax=ax, vmax=vmax, cmap=cmap)  # , vmax=vmax ,  legend=True
    #         # merged_gdf.plot(column=hour_column, ax=ax, cmap=cmap)
    #         hour_24_pop.append(target_hourly_pop_df[hour_column].sum())
    #         used_ax_cnt += 1
    
    # ax=axs[0, 0]
    # ax.axis('off')
    # ax.set_title(f"ACS 2019 Population")
    # merged_gdf = target_blockgroup_gdf.merge(target_pop_df, left_on='CBG', right_on='CBG_FIPS')
    # # merged_gdf.plot(column='totalpopulation', ax=ax,  cmap=cmap) # , vmax=vmax ,  legend=True
    # merged_gdf.plot(column='totalpopulation', ax=ax, vmax=vmax, cmap=cmap)
    
    # # draw county-level population
    # ax=axs[1, 0]
    # # ax.axis('off')
    # ax.set_title('County hourly population')
    # ax.set_ylabel('Population')
    # ax.set_xlabel('Hour')
    # ax.plot(hour_24_pop, label='hourly population')

    
     
    # fig.suptitle(f"Hourly population of county {target_county}: {year}-{month:02}-{day:02}", fontsize=24, y=1)
    
    
    # # Add colorbar axes at the bottom and align it with the left and right of the subplots
    # pos1 = axs[0, 0].get_position() # get the original position for first axis
    # pos2 = axs[-1, -1].get_position()
    # cax = fig.add_axes([pos1.x0 * 1.01, 0, (pos2.x1 - pos1.x0) * 0.99, 0.008])    # [left, bottom, width, height]  # bottom
    # value_max =vmax
    # value_min = 0
    
    # sm = plt.cm.ScalarMappable(cmap=cmap, norm=plt.Normalize(vmin=value_min, vmax=value_max))
    # sm._A = []
    # # plt.colorbar(sm, cax=cax, label="Bias")
    # cbar = plt.colorbar(sm, cax=cax, orientation='horizontal')
    
    # for t in cbar.ax.get_xticklabels():
    #     t.set_fontsize(16)
    
    # cbar.set_label('Population', labelpad=-80,   rotation=0, fontsize=24, loc='center')



    

    png_name = os.path.join(save_dir, f"{target_county.replace(', ', '_')}_hourly_population_{year}{month:02}.png")
    
    print("PNG name:", png_name)
    
    plt.savefig(png_name, dpi=300, bbox_inches='tight', pad_inches=0.2)
    # plt.close()


target_county_list = ['New York, NY']

mask = county_df['county_state'].isin(target_county_list)
target_county_df = county_df[mask]
target_county_dict = target_county_df.set_index(['county_state'])['GEOID'].to_dict()

for target_county, FIPS in tqdm(target_county_dict.items()):
# for target_county, FIPS in tqdm(county_FIPS_dict.items()):
    print(target_county)
    draw_county_map(target_county)
    
    break

print("Done")

  0%|                                                                                            | 0/1 [00:00<?, ?it/s]

New York, NY
target_counties: ['36061']
PNG name: D:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\Wild_fire\hourly_map_test_2024_home_panel_2018\visualization\New York_NY_hourly_population_202408.png


C:\Users\A\AppData\Local\Temp\ipykernel_5376\2497072873.py:167: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  plt.savefig(png_name, dpi=300, bbox_inches='tight', pad_inches=0.2)
  0%|                                                                                            | 0/1 [00:13<?, ?it/s]


ValueError: Image size of 9515x92511 pixels is too large. It must be less than 2^16 in each direction.

d:\ProgramData\anaconda3\envs\geo\lib\site-packages\IPython\core\events.py:93: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  func(*args, **kwargs)
d:\ProgramData\anaconda3\envs\geo\lib\site-packages\IPython\core\pylabtools.py:152: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  fig.canvas.print_figure(bytes_io, **kw)


In [38]:
# 31*24